In [4]:

import os
os.environ['CUDA_LAUNCH_BLOCKING'] = '0'
os.environ['CUDA_VISIBLE_DEVICES'] = '2,3'
import torch

# 确保PyTorch能够检测到GPU

In [5]:

import json
import time
import re
import itertools
import numpy as np
import pandas as pd
import datetime as DT
from tqdm import tqdm
from datetime import datetime
from scipy.optimize import curve_fit
from transformers import AutoModelForCausalLM, AutoTokenizer
from sentence_transformers import SentenceTransformer

In [7]:

# Load pretrained LLM
QWEN2d5_7B_INST = "/data/liangyunfei/Qwen2.5-7B-Instruct-AWQ"
QWEN2d5_32B_INST_AWQ = "/home/peizhengqi/Qwen/Qwen2.5-32B-Instruct-AWQ"
QWEN2d5_72B_INST_AWQ = "/data/liangyunfei/Qwen2.5-72B-Instruct-AWQ"

#model_7Bn = AutoModelForCausalLM.from_pretrained(QWEN2d5_7B_INST, device_map="auto")
#tokenizer_7Bn = AutoTokenizer.from_pretrained(QWEN2d5_7B_INST, device_map="auto")

model_32Bn = AutoModelForCausalLM.from_pretrained(QWEN2d5_7B_INST, device_map="auto")
tokenizer_32Bn = AutoTokenizer.from_pretrained(QWEN2d5_7B_INST, device_map="auto")

#model_72Bn = AutoModelForCausalLM.from_pretrained(QWEN2d5_72B_INST_AWQ, device_map="auto")
#tokenizer_72Bn = AutoTokenizer.from_pretrained(QWEN2d5_72B_INST_AWQ, device_map="auto")

OSError: Incorrect path_or_model_id: '/data/liangyunfei/Qwen2.5-7B-Instruct-AWQ'. Please provide either the path to a local folder or the repo_id of a model on the Hub.

In [ ]:

from transformers import TextStreamer

streamer = TextStreamer(tokenizer_32Bn, skip_prompt=True, skip_special_tokens=True)

NameError: name 'tokenizer_32Bn' is not defined

In [ ]:
chat_path = "./data/营养成分表/各种食物营养成分表.xls"  # (完整版)普通食物营养成分表.xls 各种食物营养成分表.xls 中国普通食物营养成分表(修正版).xls 
cost_excel = pd.read_excel(chat_path)
cost_excel

食物/100克  能量/kal  蛋白质/克  糖类/克   脂肪/克  水分/克  纤维/克  灰份/克  VA/微克  胡萝卜素/微克  \
0         VC啤酒    34.0    0.3   0.0    0.0   0.0  0.00   0.1      0        0   
1           艾菜    21.0    1.9   2.7    0.3  93.0  1.20   0.9      0     1510   
2          艾窝窝   190.0    4.3  43.1    0.0  52.1  0.29   0.2      0        0   
3           鹌鹑   110.0   20.2   0.2    3.1  75.1  0.00   1.4     40        0   
4          鹌鹑蛋   160.0   12.8   2.1   11.1  73.0  0.00   1.0    337        0   
...        ...     ...    ...   ...    ...   ...   ...   ...    ...      ...   
1720       紫雪糕   228.0    2.6  23.6   13.7  59.4  0.00   0.7     26        0   
1721       棕榈油   900.0    0.0   0.0  100.0   0.0  0.00   0.0      0        0   
1722      醉春风酒   344.0    0.0   0.0    0.0   0.0  0.00   0.0      0        0   
1723  醉流霞(57度)    62.0    0.1   0.0    0.0   0.0  0.00   0.1      0        0   
1724        鳟鱼    99.0   18.6   0.2    2.6  77.0  0.00   1.6    206        0   

      ...   钾/毫克   钠/毫克   钙/毫克  镁/毫克  铁/毫克  锰/毫克  锌/毫克  铜/毫克   磷/毫克   硒/微克  
0     ...   75.0   25.0    0.0   0.0   0.0  0.00  0.25  0.00    0.0   0.00  
1     ...  220.0  161.3   73.0  20.0   2.5  0.28  0.35  0.06   36.0   0.60  
2     ...   53.0    1.7   19.0  13.0   0.5  0.35  0.32  0.76   34.0   1.55  
3     ...  204.0   48.4   48.0  20.0   2.3  0.08  1.19  0.10  179.0  11.67  
4     ...  138.0  106.6   47.0  11.0   3.2  0.04  0.61  0.09  180.0  25.48  
...   ...    ...    ...    ...   ...   ...   ...   ...   ...    ...    ...  
1720  ...  124.0   65.9  168.0  16.0   0.8  0.08  0.60  0.04   64.0   3.35  
1721  ...    0.0    1.3    0.0   0.0   3.1  0.01  0.08  0.00    8.0   0.00  
1722  ...    0.0    0.8    3.0   1.0   0.1  0.00  0.09  0.03    0.0   0.00  
1723  ...   12.0    2.8   23.0   4.0   0.0  0.01  0.00  0.03    1.0   0.06  
1724  ...  688.0  110.0   34.0  45.0   0.0  0.07  4.30  0.18  374.0  20.40  

[1725 rows x 26 columns]

In [ ]:
file_path = './data/中国糖尿病医学营养治疗指南（2022版）(1).pdf' 
import fitz  # PyMuPDF

def read_pdf1(file_path):
    document = fitz.open(file_path)
    text = ""
    for page_num in range(len(document)):
        page = document.load_page(page_num)
        text += page.get_text()
    return text


In [ ]:
chat_path = "./data/营养成分表/(完整版)普通食物营养成分表.xls"  # (完整版)普通食物营养成分表.xls 各种食物营养成分表.xls 中国普通食物营养成分表(修正版).xls 
raw_excel = pd.read_excel(chat_path)



In [ ]:
cost_list = ['100克' + a + '包含：' + '能量'+str(b)+'卡、'+ '蛋白质'+str(c)+'克、'+ '糖类'+str(d)+'克、'+ '脂肪'+str(d)+'克' for a, b, c, d, e in zip(cost_excel['食物/100克'], cost_excel['能量/kal'], cost_excel['蛋白质/克'], cost_excel['糖类/克'], cost_excel[ '脂肪/克'])]

NameError: name 'cost_excel' is not defined

In [ ]:
chat_path = "./data/caipu.xlsx"  # (完整版)普通食物营养成分表.xls 各种食物营养成分表.xls 中国普通食物营养成分表(修正版).xls 
raw_excel = pd.read_excel(chat_path)
raw_excel = raw_excel.fillna('')

In [ ]:

caipu_list = [x +'：' + y.replace('#','').replace('\n','，') for x, y in zip(raw_excel['title'], raw_excel['yl'])]
#caipu_list = [x +'：' + y.replace('#','').replace('\n','，') + '\n做法：\n' + z.replace('#','') for x, y, z in zip(raw_excel['title'][:1000], raw_excel['yl'][:1000], raw_excel['steptext'][:1000])]
print(caipu_list)  # 输出: [5, 7, 9]


['肉末茄子煲：', '迷迭香：干煸菜花：花菜，五花肉，青蒜，红米椒，绿米椒，干辣椒，料酒，盐', '雅客茶拌：去脂奶粉，植脂末，法式香草味植脂末，白糖，雅客巴经典锡兰茶，姜粉，肉桂粉，丁香粉，小豆蔻粉', '妈妈牌健康午餐肉 好吃到没朋友：蘑菇，鸡蛋，洋葱，瘦肉沫，胡萝卜，蛋清，米饭，玉米淀粉', '家常炸酱面：五花肉 （去皮，切丁），香菇（泡发，切丁），一根葱，姜末，蒜末，新鲜小黄瓜 切丝，胡萝卜 切丝，干黄酱 （我用了Miso），甜面酱，糖', '超简单省事咖喱饭：土豆，胡萝卜，洋葱，牛肉，咖喱块', '孜然香烤豆腐：北豆腐，生抽，孜然，辣椒粉，熟芝麻，椒盐', '果蔬沙拉：生菜，苹果，梨，草莓，熟鸡蛋，红萝卜，黄瓜，坚果，黑芝麻，沙拉酱', '芋圆红豆汤：紫薯，芋头，牛奶，红豆，白砂糖', '金牌BBQ烤鱿鱼筒：冰冻鱿鱼，金牌BBQ烤肉料，花生油，柠檬片，薄荷叶', '冷吃牛肉：牛里脊肉，油，生姜，八角，山奈，料酒，盐，糖，红酱油，辣椒油，花椒', '酸汤麻辣小面—迷迭香：辣椒油，花椒油，辣椒碎，蒜泥，醋，生抽，白芝麻，盐', '龙猫*烧果子：蛋黄，泡打粉，红豆馅，巧克力，食用色油', '茄汁藕饼：藕，五花肉馅，葱花姜末，盐味糖，味极鲜，黑胡椒，白胡椒，黄酒，芝麻油，蛋清，淀粉，番茄，番茄沙司，老抽，蚝油，蒜末', '年夜饭_清蒸鲈鱼：姜，香葱，料酒，盐，蚝油，蒸鱼豉油，猪油，花椒，柠檬汁', '凉拌菜豆笋（腐竹）：腐竹，辣椒油，蒜，葱，辣椒粉', '饭合 | 橙味鸭胸：鸭胸肉，小番茄，茴香头，橙子，盐，黑胡椒，橄榄油，意大利黑醋，五香粉，大蒜，姜片', '红酒香煎龙利鱼：龙利鱼，洋葱，香葱，柠檬，指天椒，红酒，黑胡椒，白糖，料酒，酱油，蚝油，姜水，淀粉', '♡夏至粥♡：小米，荞麦，红豆，糯米，燕麦，薏米，大红豆，芸豆，糙米，绿豆，大米，白糖，小米', '女王私厨 | 豆芽饭：大米，豆芽，韭菜，水，酱油，辣椒粉，香油，芝麻', '丝瓜鲜虾盅#元气挑战美一天#：鲜虾，丝瓜，剁椒（不吃辣就不放），生抽，蚝油，香油，白糖，料酒，盐', '红烧扁鱼：扁鱼，生姜，大蒜，豆瓣酱，黄酒，酱油，干辣椒', '干锅土豆片：五花肉，土豆，红萝卜，青椒，青蒜，姜葱蒜，生抽，红辣椒，料酒，孜然粉，油盐', '鱼香肉丝：猪里脊肉，冬笋，胡萝卜，黑木耳，葱末，姜末，蒜末，剁椒，水淀粉

In [ ]:
distance_list = [edit_distance('白菜', food_name) for food_name in raw_excel['title']]

In [ ]:
def edit_distance(str1, str2):
    m = len(str1)
    n = len(str2)
    
    # 创建一个 (m+1) x (n+1) 的矩阵来存储子问题的解
    dp = [[0] * (n + 1) for _ in range(m + 1)]
    # 初始化边界条件
    for i in range(m + 1):
        dp[i][0] = i  # str1的前i个字符变成空字符串需要i次删除操作
    for j in range(n + 1):
        dp[0][j] = j  # 空字符串变成str2的前j个字符需要j次插入操作
    # 填充dp表
    for i in range(1, m + 1):
        for j in range(1, n + 1):
            if str1[i - 1] == str2[j - 1]:
                dp[i][j] = dp[i - 1][j - 1]  # 如果字符相同，不需要额外操作
            else:
                dp[i][j] = min(dp[i - 1][j] + 1,    # 删除操作
                               dp[i][j - 1] + 1,    # 插入操作
                               dp[i - 1][j - 1] + 1)  # 替换操作
    return dp[m][n]

In [ ]:
def get_KB_list(food_list):
    KB_list = []
    for target_name in food_list:
        distance_list = [edit_distance(target_name, food_name) for food_name in raw_excel['title']]
        min_value = min(distance_list)
        target_food = [caipu_list[index] for index, value in enumerate(distance_list) if value == min_value]
        content_list = [content.split('：')[1].split('，') for content in target_food]
        content_list_all = []
        for sub_list in content_list:
            content_list_all += sub_list
        content_list_all = list(set(content_list_all))
        title_list = list(cost_excel['食物/100克'])
        last_content_list = [cost_list[title_list.index(name)] for name in content_list_all if name in title_list]
        KB_list += target_food
        KB_list += last_content_list
    return KB_list

In [ ]:
get_KB_list(['白菜', '红薯'])

NameError: name 'caipu_list' is not defined

In [ ]:
'我今天吃了白菜和红薯怎么样'

In [ ]:
KB_list = []
KB_list += target_food + last_content_list
KB_list

In [ ]:

content_list_all = []
for sub_list in content_list:
    content_list_all += sub_list
content_list_all

In [ ]:
book = read_pdf1(file_path)

In [ ]:

sys_prompt1 = """
    You are a helpful, respectful and honest assistant. 
    Always answer as helpfully as possible, while being safe. 
    Your answers should not include any harmful, unethical, racist, sexist, toxic, dangerous, or illegal content. 
    Please ensure that your responses are socially unbiased and positive in nature.
    If you don't know the answer to a question, please don't share false information.
"""


def message_to_response_via_LLM(model, tokenizer, messages, max_new_tokens=256):

    text = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)
    model_inputs = tokenizer([text], return_tensors="pt").to(model.device)

    generated_ids = model.generate(model_inputs.input_ids, max_new_tokens=max_new_tokens, do_sample=True, temperature=0.01, streamer=streamer)
    generated_ids = [output_ids[len(input_ids):] for input_ids, output_ids in zip(model_inputs.input_ids, generated_ids)]
    response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]

    return response

In [ ]:
with open('food.txt','r') as f:
    food_list = f.readlines()

In [ ]:
i

In [ ]:
query_prompt = '从中抽取和饮食相关的规范'#input()#"我吃的是咖喱饭"
print('患者：')
print(query_prompt)
format_prompt = "将抽取出来的规则用'，'隔开"
all_rules = ''
for i in range(0, len(book), 10000):
    res_messages = [
        {"role": "system", "content": sys_prompt1},
        {"role": "user", "content": '给定一本关于糖尿病饮食的书'+book[:i+10000]},
        #{"role": "assistant", "content": '肉末茄子煲，可乐'},
        {"role": "user", "content": query_prompt+format_prompt}
    ]
    torch.cuda.empty_cache()
    llm_response = message_to_response_via_LLM(model_32Bn, tokenizer_32Bn, res_messages, max_new_tokens=1000)
    all_rules += llm_response

In [ ]:
query_prompt = '请问吃咖喱饭和可乐怎么样'#input()#"我吃的是咖喱饭"
print('患者：')
print(query_prompt)
format_prompt = "请只回答上去话中的食物，并用'，'隔开"

res_messages = [
    {"role": "system", "content": sys_prompt1},
    {"role": "user", "content": '请问吃肉末茄子煲和可乐怎么样'},
    {"role": "assistant", "content": '肉末茄子煲，可乐'},
    {"role": "user", "content": query_prompt+format_prompt}
]
output_food = message_to_response_via_LLM(model_32Bn, tokenizer_32Bn, res_messages, max_new_tokens=1000)



In [ ]:
get_KB_list(output_food.split('，'))

In [ ]:
'盐' in list(cost_excel['食物/100克'])

In [ ]:
format_prompt = f"如果吃{output_food}的话，严格按照给出的组成成分还有营养含量list，输出食物的组成成分和营养含量并给出建议，如果list中没有某个食物则不对这个食物进行评价"
res_messages = [
    {"role": "system", "content": sys_prompt1},
    {"role": "user", "content": "给定一个每种食物的组成成分还有营养含量list：" +'\n'.join(get_KB_list(output_food.split('，')))}, 
    {"role": "user", "content": format_prompt}
]
llm_response = message_to_response_via_LLM(model_32Bn, tokenizer_32Bn, res_messages, max_new_tokens=1000)

In [ ]:

query_prompt = '请问肉末茄子煲怎么做'#input()#"我吃的是咖喱饭"
print('患者：')
print(query_prompt)
print('医生：')

bg_prompt = "已知今天的日期是：{}，北京时间。".format(time.asctime(time.localtime()))
format_prompt = "请严格按照食物组成成分和做法list，简短的回答我"


res_messages = [
    {"role": "system", "content": sys_prompt1},
    {"role": "user", "content": "给定一个每种食物的组成成分和做法list：" +'\n'.join(caipu_list[:10])}, #+str(context_list)
    {"role": "user", "content": query_prompt+format_prompt}
]
llm_response = message_to_response_via_LLM(model_32Bn, tokenizer_32Bn, res_messages, max_new_tokens=1000)

In [ ]:
print(1)

In [ ]:
query_prompt = '请问一斤菠菜和一斤菠萝分别含有多少能量、蛋白质、糖类、脂肪'#input()#"我吃的是咖喱饭"
print('患者：')
print(query_prompt)
print('医生：')

bg_prompt = "已知今天的日期是：{}，北京时间。".format(time.asctime(time.localtime()))
format_prompt = "请严格按照食物组成成分和做法list，简短的回答我，脂肪和蛋白质不要算错了"


res_messages = [
    {"role": "system", "content": sys_prompt1},
    {"role": "user", "content": "给定一个每种食物的组成成分和做法list：" +'\n'.join(cost_list[:100])}, #+str(context_list)
    {"role": "user", "content": query_prompt+format_prompt}
]
llm_response = message_to_response_via_LLM(model_32Bn, tokenizer_32Bn, res_messages, max_new_tokens=1000)